# **Creating the Dimensional and Fact tables** 

**1\. Always start with the dimensional tables first**

In [24]:
USE AdventureWorksDW

drop table if exists TerritoryDim;

Create TABLE TerritoryDim(
    SKey INT NOT NULL IDENTITY(1,1) PRIMARY KEY,
    TerritoryID int not null,
    TerritoryName nvarchar(50),
    CountryRegionCode nvarchar(3) not null,
    CountryRegionName nvarchar(50),
    StateProvinceID int not null,
    StateProvinceCode nvarchar(3),
    City nvarchar(30) ,
    PostalCode nvarchar(15),
    ETL_Load_time DATETIME DEFAULT GETUTCDATE()
)

Commands completed successfully.

Total execution time: 00:00:00.007

In [25]:
USE AdventureWorksDW

drop table if exists ProductDimension;

Create TABLE ProductDimension(
SKey INT NOT NULL IDENTITY(1,1) PRIMARY KEY,
ProductID int not null,
[Name] nvarchar(50) not null,
ProductNumber nvarchar(25),
FinishedGoodsFlag bit not null,
Color nvarchar(15) default ('Not Specified'),
ProductCategoryID int not null,
ProductCategoryName nvarchar(50) default ('Not Specified'),
ProductSubCategoryID int not null ,
ProductSubcategoryName nvarchar(50),
ProductModelID int ,
ProductModelName nvarchar(50) default ('Not Specified'),
ProductDescriptionID int,
ProductDescription nvarchar(400) default ('Not Specified'),
CatalogDescription XML default ('Not Specified'),
Instructions XML default ('Not Specified'),
ModifiedDate datetime default ('Not Specified'),
[Weight] decimal(8,2) default (0),
WeightUnitMeasureCode nchar(3) DEFAULT(0),
[Size] nvarchar(5) default ('Not Specified'),
UnitPrice money not null,
UnitDiscountPrice money DEFAULT(0),
ETL_Load_Time DATETIME DEFAULT GETUTCDATE()
);

Commands completed successfully.

Total execution time: 00:00:00.013

In [26]:
USE AdventureWorksDW

drop table if exists DateDimension;

CREATE TABLE DateDimension(
    SKey INT NOT NULL IDENTITY(1,1) PRIMARY KEY,
    [Day] INT,
    [Month] INT,
    [Year] INT,
    [Quarter] INT,
    ETL_Load_Time DATETIME DEFAULT GETUTCDATE()
);


Commands completed successfully.

Total execution time: 00:00:00.005

In [27]:
USE AdventureWorksDW

drop table if EXISTS ShipingDimension;

create table ShipingDimension(
    SKey INT NOT NULL IDENTITY(1,1) PRIMARY KEY,
    ShipMethodID int not null,
    [Name]  nvarchar(50),
    ShipBase money,
    ShipRate money,
    ShipDate datetime,
    [Status] tinyint,
    ETL_Load_Time DATETIME DEFAULT GETUTCDATE()
)

Commands completed successfully.

Total execution time: 00:00:00.005

In [6]:
use AdventureWorksDW

drop TABLE if EXISTS 

create table OrderFactTable(
    TerritoryDimKey int,
    ProductDimKey int, 
    DateDimKey int,
    ShippingDimKey int,
    OrderQuantity int,
    TotalAmount decimal(8,2),
    ETL_Load_Time DATETIME DEFAULT GETUTCDATE()
)

Commands completed successfully.

Total execution time: 00:00:00.002

Populating the tables

In [19]:
ALTER TABLE AdventureWorksDW.dbo.TerritoryDim
alter column TerritoryName NVARCHAR(50)

Commands completed successfully.

Total execution time: 00:00:00.005

# **Inital Inserting in the Dimensions and Fact tables**

**Script for populating the Date dimension with every day from 2013 to 2014 (this is part of the data from the operational db, becouse we store it locally there is no need to store all the data).**

In [ ]:
USE AdventureWorksDW

DECLARE @StartDate DATE = '2013-01-01';
DECLARE @EndDate DATE = '2014-12-31';

WHILE @StartDate <= @EndDate
BEGIN
    INSERT INTO DateDimension ([Day], [Month], [Year], [Quarter])
    VALUES (
        DAY(@StartDate),
        MONTH(@StartDate),
        YEAR(@StartDate),
        DATEPART(QUARTER, @StartDate)
    );
    SET @StartDate = DATEADD(DAY, 1, @StartDate);
END;

- Adding data to the Territory dimension

In [29]:
use AdventureWorksDW

;with source_territory as (
    SELECT st.TerritoryID,
        st.Name as territory_name,
        cr.CountryRegionCode ,
        cr.Name as countryRegionName,
        sp.StateProvinceID,
        sp.StateProvinceCode,
        ad.City,
        ad.PostalCode,
        GETUTCDATE() AS ETL_LoadTime
    FROM (((AdventureWorks2022.Sales.SalesTerritory AS st 
    JOIN AdventureWorks2022.Person.CountryRegion AS cr ON 
    st.CountryRegionCode = cr.CountryRegionCode) 
    LEFT JOIN AdventureWorks2022.Person.StateProvince AS sp ON
    sp.TerritoryID = st.TerritoryID)
    LEFT JOIN AdventureWorks2022.Person.Address AS ad ON
    ad.StateProvinceID = sp.StateProvinceID)   
)
INSERT into AdventureWorksDW.dbo.TerritoryDim
select st.*
from source_territory as st
left join AdventureWorksDW.dbo.TerritoryDim as td on st.TerritoryID = td.TerritoryID 
where td.SKey is null;

(19721 rows affected)

Total execution time: 00:00:00.077

- Adding data to the Product Dimension

In [33]:
use AdventureWorksDW

;with source_product as(
    SELECT p.ProductID ,
        p.[Name],
        p.ProductNumber,
        p.FinishedGoodsFlag ,
        p.Color ,
        pc.ProductCategoryID,
        pc.Name as ProductCategoryName ,
        psc.ProductSubCategoryID,
        psc.Name as ProductSubcategoryName ,
        pm.ProductModelID  ,
        pm.Name as ProductModelName,
        pmpdc.ProductDescriptionID ,
        pd.Description as ProductDescription ,
        pm.CatalogDescription ,
        pm.Instructions ,
        p.ModifiedDate ,
        p.[Weight] ,
        p.WeightUnitMeasureCode,
        p.[Size] ,
        sod.UnitPrice,
        sod.UnitPriceDiscount as UnitDiscountPrice ,
        GETUTCDATE() as ETL_Load_Time

    from ((((((AdventureWorks2022.Sales.SalesOrderDetail as sod 
    left join AdventureWorks2022.Production.Product as p on
    sod.ProductID = p.ProductID)   
    join AdventureWorks2022.Production.ProductSubCategory as psc on 
    p.ProductSubcategoryID = psc.ProductSubcategoryID)
    join AdventureWorks2022.Production.ProductCategory as pc on 
    psc.ProductCategoryID = pc.ProductCategoryID)
    join AdventureWorks2022.Production.ProductModel as pm ON
    p.ProductModelID = pm.ProductModelID)
    join AdventureWorks2022.Production.ProductModelProductDescriptionCulture as pmpdc on
    pmpdc.ProductModelID = pm.ProductModelID )
    join AdventureWorks2022.Production.ProductDescription as pd on 
    pd.ProductDescriptionID = pmpdc.ProductDescriptionID)
)
INSERT INTO AdventureWorksDW.dbo.ProductDimension
select sp.*
from source_product as sp
left join AdventureWorksDW.dbo.ProductDimension as pd on sp.ProductID = pd.ProductID  
where pd.SKey is null;


(727224 rows affected)

Total execution time: 00:00:09.232

- Adding data to the Shipping Dimension

In [10]:
use AdventureWorksDW 

;With ship_method_source as (
select sm.ShipMethodID,
    sm.[Name],
    sm.ShipBase,
    sm.ShipRate,
    poh.ShipDate,
    poh.[Status],
    GETUTCDATE() as ETL_Load_Time
    from AdventureWorks2022.Purchasing.PurchaseOrderHeader as poh 
    left join AdventureWorks2022.Purchasing.ShipMethod as sm 
    on poh.ShipMethodID = sm.ShipMethodID )
    INSERT INTO AdventureWorksDW.dbo.ShipingDimension
    select sms.*
    from ship_method_source as sms
    left join AdventureWorksDW.dbo.ShipingDimension as sd on sms.ShipMethodID = sd.ShipMethodID
    where sd.SKey is NULL ; 


(0 rows affected)

Total execution time: 00:00:00.230

- Creating a temporary table to get the natural keys of the dimensions from the operational database

In [3]:
  Use AdventureWorks2022
  
  SELECT soh.TerritoryID,
    sod.ProductID, 
    soh.ShipMethodID,
    DAY(soh.OrderDate) as [Day],
    MONTH(soh.OrderDate) as [Month],
    YEAR(soh.OrderDate)  as  [Year],
    sod.OrderQty,
    sod.UnitPrice
    FROM (AdventureWorks2022.Sales.SalesOrderDetail as sod 
    JOIN AdventureWorks2022.Sales.SalesOrderHeader as soh 
    ON sod.SalesOrderID = soh.SalesOrderID)

(121317 rows affected)

Displaying Top 5000 rows.

Total execution time: 00:00:00.647

TerritoryID ProductID ShipMethodID Day Month Year OrderQty UnitPrice 5 776 5 31 5 2011 1 2024.994 5 777 5 31 5 2011 3 2024.994 5 778 5 31 5 2011 1 2024.994 5 771 5 31 5 2011 1 2039.994 5 772 5 31 5 2011 1 2039.994 5 773 5 31 5 2011 2 2039.994 5 774 5 31 5 2011 1 2039.994 5 714 5 31 5 2011 3 28.8404 5 716 5 31 5 2011 1 28.8404 5 709 5 31 5 2011 6 5.70 5 712 5 31 5 2011 2 5.1865 5 711 5 31 5 2011 4 20.1865 5 762 5 31 5 2011 1 419.4589 5 758 5 31 5 2011 1 874.794 6 745 5 31 5 2011 1 809.76 6 743 5 31 5 2011 1 714.7043 6 747 5 31 5 2011 2 714.7043 6 712 5 31 5 2011 4 5.1865 6 715 5 31 5 2011 4 28.8404 6 742 5 31 5 2011 2 722.5949 6 775 5 31 5 2011 3 2024.994 6 778 5 31 5 2011 2 2024.994 6 711 5 31 5 2011 2 20.1865 6 741 5 31 5 2011 2 818.70 6 776 5 31 5 2011 4 2024.994 6 773 5 31 5 2011 2 2039.994 6 716 5 31 5 2011 2 28.8404 6 777 5 31 5 2011 2 2024.994 6 708 5 31 5 2011 5 20.1865 6 764 5 31 5 2011 3 419.4589 6 770 5 31 5 2011 5 419.4589 6 730 5 31 5 2011 2 183.9382 6 754 5 31 5 2011 4 874.794 6 725 5 31 5 2011 3 183.9382 6 762 5 31 5 2011 5 419.4589 6 765 5 31 5 2011 3 419.4589 6 768 5 31 5 2011 2 419.4589 6 753 5 31 5 2011 1 2146.962 6 756 5 31 5 2011 1 874.794 6 763 5 31 5 2011 3 419.4589 6 732 5 31 5 2011 1 356.898 6 758 5 31 5 2011 6 874.794 6 729 5 31 5 2011 1 183.9382 6 722 5 31 5 2011 3 178.5808 6 749 5 31 5 2011 1 2146.962 6 760 5 31 5 2011 3 419.4589 6 726 5 31 5 2011 1 183.9382 6 733 5 31 5 2011 1 356.898 6 738 5 31 5 2011 1 178.5808 6 766 5 31 5 2011 3 419.4589 6 755 5 31 5 2011 1 874.794 4 760 5 31 5 2011 1 419.4589 1 772 5 31 5 2011 1 2039.994 1 775 5 31 5 2011 4 2024.994 1 714 5 31 5 2011 1 28.8404 1 716 5 31 5 2011 1 28.8404 1 777 5 31 5 2011 2 2024.994 1 771 5 31 5 2011 3 2039.994 1 773 5 31 5 2011 1 2039.994 1 778 5 31 5 2011 1 2024.994 1 711 5 31 5 2011 2 20.1865 1 773 5 31 5 2011 1 2039.994 1 707 5 31 5 2011 1 20.1865 1 715 5 31 5 2011 2 28.8404 1 777 5 31 5 2011 2 2024.994 1 712 5 31 5 2011 2 5.1865 1 775 5 31 5 2011 2 2024.994 1 778 5 31 5 2011 1 2024.994 1 709 5 31 5 2011 6 5.70 1 776 5 31 5 2011 1 2024.994 4 764 5 31 5 2011 1 419.4589 4 753 5 31 5 2011 1 2146.962 4 732 5 31 5 2011 1 356.898 4 756 5 31 5 2011 1 874.794 4 768 5 31 5 2011 2 419.4589 4 766 5 31 5 2011 1 419.4589 3 710 5 31 5 2011 3 5.70 3 773 5 31 5 2011 1 2039.994 3 778 5 31 5 2011 1 2024.994 3 775 5 31 5 2011 1 2024.994 6 756 5 31 5 2011 3 874.794 6 753 5 31 5 2011 2 2146.962 6 760 5 31 5 2011 7 419.4589 6 765 5 31 5 2011 6 419.4589 6 715 5 31 5 2011 6 28.8404 6 730 5 31 5 2011 6 183.9382 6 707 5 31 5 2011 2 20.1865 6 711 5 31 5 2011 2 20.1865 6 754 5 31 5 2011 2 874.794 6 712 5 31 5 2011 4 5.1865 6 729 5 31 5 2011 2 183.9382 6 755 5 31 5 2011 3 874.794 6 761 5 31 5 2011 3 419.4589 6 770 5 31 5 2011 2 419.4589 6 726 5 31 5 2011 3 183.9382 6 764 5 31 5 2011 2 419.4589 6 766 5 31 5 2011 2 419.4589 6 725 5 31 5 2011 2 183.9382 6 716 5 31 5 2011 1 28.8404 6 768 5 31 5 2011 2 419.4589 6 732 5 31 5 2011 4 356.898 6 758 5 31 5 2011 6 874.794 6 762 5 31 5 2011 4 419.4589 6 738 5 31 5 2011 3 178.5808 6 714 5 31 5 2011 4 28.8404 6 722 5 31 5 2011 3 178.5808 6 708 5 31 5 2011 1 20.1865 6 733 5 31 5 2011 3 356.898 6 763 5 31 5 2011 3 419.4589 1 747 5 31 5 2011 1 714.7043 3 710 5 31 5 2011 1 5.70 3 709 5 31 5 2011 2 5.70 3 773 5 31 5 2011 2 2039.994 3 776 5 31 5 2011 1 2024.994 1 753 5 31 5 2011 1 2146.962 1 714 5 31 5 2011 2 28.8404 1 756 5 31 5 2011 1 874.794 1 768 5 31 5 2011 2 419.4589 1 732 5 31 5 2011 2 356.898 1 763 5 31 5 2011 2 419.4589 1 755 5 31 5 2011 2 874.794 1 764 5 31 5 2011 2 419.4589 1 716 5 31 5 2011 1 28.8404 1 711 5 31 5 2011 1 20.1865 1 708 5 31 5 2011 1 20.1865 6 709 5 31 5 2011 6 5.70 6 776 5 31 5 2011 2 2024.994 6 774 5 31 5 2011 1 2039.994 2 754 5 31 5 2011 1 874.794 2 715 5 31 5 2011 3 28.8404 2 729 5 31 5 2011 1 183.9382 2 761 5 31 5 2011 2 419.4589 2 762 5 31 5 2011 1 419.4589 2 738 5 31 5 2011 2 178.5808 2 770 5 31 5 2011 2 419.4589 2 712 5 31 5 2011 1 5.1865 2 708 5 31 5 2011 2 20.1865 2 711 5 31 5 2011 1 20.1865 2 707 5 31 

In [3]:

;with fact_cte as(
    SELECT soh.TerritoryID,
    sod.ProductID, 
    soh.ShipMethodID,
    DAY(soh.OrderDate) as [Day],
    MONTH(soh.OrderDate) as [Month],
    YEAR(soh.OrderDate)  as  [Year],
    sod.OrderQty,
    sod.UnitPrice
    FROM (AdventureWorks2022.Sales.SalesOrderDetail as sod 
    JOIN AdventureWorks2022.Sales.SalesOrderHeader as soh 
    ON sod.SalesOrderID = soh.SalesOrderID)
)SELECT 
        fcte.TerritoryID,
        fcte.ProductID,
        fcte.ShipMethodID,
        fcte.Day,
        fcte.Month,
        fcte.Year,
        SUM(fcte.OrderQty) AS TotalQuantity,
        SUM(fcte.OrderQty * fcte.UnitPrice) AS TotalAmount
INTO #Tmp_FactOrder
FROM fact_cte fcte
GROUP BY fcte.TerritoryID,
        fcte.ProductID,
        fcte.ShipMethodID,
        fcte.Day,
        fcte.Month,
        fcte.Year;

(69202 rows affected)

Total execution time: 00:00:00.308

In [4]:
Select * from #Tmp_FactOrder;

(69202 rows affected)

Displaying Top 5000 rows.

Total execution time: 00:00:01.227

TerritoryID ProductID ShipMethodID Day Month Year TotalQuantity TotalAmount 2 973 5 30 6 2013 16 16329.504 9 708 1 10 12 2013 1 34.99 7 711 1 12 1 2014 1 34.99 1 707 1 26 4 2014 3 104.97 10 714 1 14 6 2014 1 49.99 7 795 1 17 8 2012 1 2181.5625 1 870 1 21 7 2013 2 9.98 1 922 1 17 12 2013 1 3.99 8 882 1 6 5 2014 1 53.99 7 931 1 6 8 2013 1 21.49 8 934 1 29 8 2013 1 28.99 7 998 5 31 3 2014 11 3563.934 4 970 5 1 5 2014 6 4373.46 10 748 5 28 1 2013 4 2977.0908 9 798 1 25 5 2013 1 1000.4375 3 885 5 31 7 2013 2 1204.692 4 872 1 18 11 2013 1 8.99 8 781 1 31 12 2013 1 2319.99 6 962 5 31 3 2014 2 890.82 5 765 5 30 10 2012 11 5167.734 7 810 5 1 3 2014 2 144.324 5 707 5 1 10 2011 10 201.865 1 798 1 12 1 2013 1 1000.4375 4 780 1 12 7 2013 1 2319.99 6 872 1 9 12 2013 1 8.99 4 707 1 19 1 2014 1 34.99 1 921 1 28 5 2014 2 9.98 7 923 1 1 6 2014 1 4.99 4 711 1 7 6 2014 3 104.97 5 732 5 1 7 2011 2 713.796 3 764 5 1 1 2012 4 1677.8356 2 801 5 30 9 2013 8 5378.352 1 934 1 1 1 2014 1 28.99 4 929 1 10 2 2014 2 59.98 6 852 5 30 8 2012 23 1034.862 10 794 1 13 11 2012 2 4363.125 10 999 5 30 8 2013 5 1619.97 6 712 1 30 9 2013 2 17.98 9 977 1 18 12 2013 1 539.99 7 873 1 25 4 2014 1 2.29 9 749 1 22 8 2011 1 3578.27 10 787 5 31 7 2012 11 7127.934 4 798 1 12 11 2013 1 1120.49 7 971 1 18 1 2014 1 1214.85 4 748 5 31 12 2012 4 2977.0908 9 921 1 23 6 2013 2 9.98 9 858 1 9 10 2013 1 24.49 6 879 1 16 12 2013 1 159.00 1 770 1 13 12 2011 1 699.0982 9 880 1 8 9 2013 2 109.98 4 929 1 28 5 2014 3 89.97 2 764 5 30 3 2012 5 2097.2945 10 791 1 3 1 2013 1 2443.35 9 882 1 12 10 2013 1 53.99 4 800 1 14 12 2013 1 1120.49 1 883 1 18 12 2013 1 53.99 4 711 1 19 2 2014 1 34.99 1 712 1 14 6 2013 1 8.99 4 881 1 9 9 2013 1 53.99 6 877 1 13 11 2013 1 7.95 10 876 5 29 1 2014 17 1224.00 4 988 5 29 1 2014 9 3050.946 9 714 5 1 3 2014 3 89.982 5 794 5 31 3 2014 4 5864.04 4 836 5 30 8 2012 8 2595.6216 7 762 5 28 2 2013 3 1409.382 5 940 5 30 6 2013 9 437.346 10 956 1 21 8 2013 1 2384.07 4 868 1 17 10 2013 1 69.99 10 871 1 20 10 2013 1 9.99 4 922 1 5 3 2014 1 3.99 6 711 1 10 3 2014 1 34.99 7 935 5 1 5 2014 4 97.176 4 775 5 1 10 2011 11 22274.934 1 825 5 30 9 2012 18 3533.922 9 880 1 26 12 2013 1 54.99 8 962 5 31 12 2013 4 1781.64 10 966 1 31 12 2013 1 2384.07 8 716 1 27 6 2013 1 49.99 7 931 1 1 2 2014 2 42.98 8 712 1 20 4 2014 4 35.96 10 784 1 20 10 2012 1 2049.0982 9 798 1 30 11 2012 1 1000.4375 6 871 1 25 11 2013 1 9.99 10 783 5 31 12 2013 2 2753.988 3 906 5 31 3 2014 1 218.454 4 905 5 31 3 2014 8 1747.632 1 933 1 5 5 2014 2 65.20 6 872 1 5 6 2014 1 8.99 1 715 1 2 7 2013 1 49.99 9 794 1 7 7 2013 1 2443.35 1 714 1 17 7 2013 1 49.99 10 923 1 28 5 2014 4 19.96 4 797 1 4 1 2014 1 1120.49 8 974 1 29 5 2014 1 1700.99 6 867 1 2 7 2013 1 69.99 4 908 5 1 3 2014 3 48.816 9 959 5 31 12 2013 4 1781.64 3 976 5 1 3 2014 13 13267.722 1 998 1 4 4 2014 2 1079.98 1 956 5 31 7 2013 4 3814.512 2 739 5 31 7 2013 1 818.70 9 873 1 3 10 2013 2 4.58 4 707 5 31 12 2013 1 20.994 4 922 1 23 6 2014 2 7.98 9 750 1 23 11 2011 1 3578.27 4 876 1 2 4 2014 2 240.00 6 748 5 29 2 2012 3 2167.7847 1 931 1 24 12 2013 2 42.98 1 875 5 1 5 2014 31 164.8766 1 708 1 10 5 2014 1 34.99 8 796 1 25 11 2012 1 2181.5625 9 712 1 9 7 2013 2 17.98 5 959 5 31 7 2013 8 2672.46 10 711 1 27 4 2014 2 69.98 1 766 5 1 12 2011 1 419.4589 1 711 1 30 5 2013 1 34.99 10 796 1 12 6 2013 1 2443.35 7 921 1 14 7 2013 1 4.99 2 907 5 30 9 2013 6 383.40 2 904 5 30 11 2013 3 655.362 1 711 1 1 12 2013 1 34.99 7 707 1 18 12 2013 1 34.99 9 880 1 3 3 2014 2 109.98 8 870 1 9 3 2014 2 9.98 9 768 1 16 3 2013 1 782.99 4 858 5 31 7 2013 9 132.246 4 869 1 1 11 2013 1 69.99 10 714 1 26 2 2014 1 49.99 4 873 1 19 8 2013 2 4.58 4 928 1 25 1 2014 1 24.99 4 782 1 10 2 2014 1 2294.99 7 872 1 6 4 2014 1 8.99 10 955 1 20 5 2014 1 2384.07 9 784 1 13 6 2013 1 2294.99 4 878 1 23 7 2013 1 21.98 10 859 1 30 8 2013 1 24.49 4 930 1 17 12 2013 3 105.00 4 780 1 25 4 2014 1 2319.99 4 865 1 13 6 2014 1 63.50 4 991 1 28 7 2013 1 539.99 7 929 1 22 10 2013 1 29.99 8 798 1 6 4 2014 2 2240.98 9 8

- Populating the fact table with the help of the temp table (we get the surogate keys with joining the temporary table's natural keys with the natural keys in the dimension tables )
- select top 100 is used so that we don't store all the data locally (60k rows is all the data)

In [5]:
use AdventureWorksDW

INSERT INTO OrderFactTable(TerritoryDimKey ,ProductDimKey,DateDimKey, ShippingDimKey, OrderQuantity ,TotalAmount)
select top 100 td.SKey as TerritoryDimKey, pd.SKey as ProductDimKey, dd.SKey as DateDimKey,sd.SKey as ShippingDimKey, fo.TotalQuantity, fo.TotalAmount
FROM TerritoryDim as td join #Tmp_FactOrder as fo on td.TerritoryID = fo.TerritoryID
JOIN ProductDimension as pd on pd.ProductID= fo.ProductID 
JOIN ShipingDimension as sd on sd.ShipMethodID = fo.ShipMethodID
JOIN DateDimension as dd on dd.[Day] = fo.Day and dd.[Month] = fo.Month and dd.[Year] = fo.Year
Left join OrderFactTable as oft on 
oft.TerritoryDimKey = td.SKey and 
oft.ProductDimKey = pd.SKey and 
oft.ShippingDimKey= sd.SKey and 
dd.SKey= oft.DateDimKey 
where oft.ProductDimKey is NULL;

(100 rows affected)

Total execution time: 01:10:50.259

# **Creating stored procedures**

- Log table for tracking

In [23]:
USE AdventureWorksDW;

drop table if exists ETL_Process_Log

CREATE TABLE ETL_Process_Log
(
    Id int identity(1,1) primary key,
    TableName NVARCHAR(50),
    ETL_start datetime default GETUTCDATE(),
    ETL_end datetime,
    NumberOfRecordsBefore int,
    NumberOfRecordsAfter int, 
    NumberOfRecordsModified int,
    NumberOfRecordsAffected as NumberOfRecordsModified + NumberOfRecordsAfter - NumberOfRecordsBefore,
    CheckpointStatus NVARCHAR(50) default 'started',
    LastModifiedDate datetime default GETUTCDATE()
)

Commands completed successfully.

Total execution time: 00:00:00.009

- Stored procedure for the TerritoryDimension

In [5]:
CREATE OR ALTER PROCEDURE ETL_Territory
AS 
BEGIN

    DECLARE @Before bigint, @After bigint, @Updated bigint
    DECLARE @start_time datetime = GETUTCDATE()

    set @Before = (select COUNT_BIG(*) from AdventureWorksDW.dbo.TerritoryDim )

    DECLARE @log_ids as table (id bigint)

    INSERT INTO AdventureWorksDW.dbo.ETL_Process_Log(TableName, ETL_start, NumberOfRecordsBefore)
    OUTPUT INSERTED.ID INTO @log_ids 
    VALUES('TerritoryDim',@start_time, @Before)

    DECLARE @LogId as bigint = (select top 1 id from @log_ids)

    ;with source_territory as (
        SELECT st.TerritoryID,
            st.Name as territory_name,
            cr.CountryRegionCode ,
            cr.Name as countryRegionName,
            sp.StateProvinceID,
            sp.StateProvinceCode,
            ad.City,
            ad.PostalCode,
            GETUTCDATE() AS ETL_LoadTime
        FROM (((AdventureWorks2022.Sales.SalesTerritory AS st 
        JOIN AdventureWorks2022.Person.CountryRegion AS cr ON 
        st.CountryRegionCode = cr.CountryRegionCode) 
        LEFT JOIN AdventureWorks2022.Person.StateProvince AS sp ON
        sp.TerritoryID = st.TerritoryID)
        LEFT JOIN AdventureWorks2022.Person.Address AS ad ON
        ad.StateProvinceID = sp.StateProvinceID)   
    )
    INSERT into AdventureWorksDW.dbo.TerritoryDim
    select st.*
    from source_territory as st
    left join AdventureWorksDW.dbo.TerritoryDim as td on st.TerritoryID = td.TerritoryID 
    where td.SKey is null;

    UPDATE AdventureWorksDW.dbo.ETL_Process_Log
    set CheckpointStatus = 'Insert new complete'
    where id = @LogId

    set @After = (SELECT COUNT_BIG(*) from AdventureWorksDW.dbo.TerritoryDim)

    set @Updated = @After - @Before

    UPDATE AdventureWorksDW.dbo.ETL_Process_Log
    SET CheckpointStatus = 'Completed',
        NumberOfRecordsAfter = @After,
        NumberOfRecordsModified = @Updated,
        LastModifiedDate = GETUTCDATE()
    WHERE id = @LogId



END

Commands completed successfully.

Total execution time: 00:00:00.012

- Creating a procedure for the Product Dimension

In [17]:
CREATE OR ALTER PROCEDURE ETL_Product
AS
BEGIN

    DECLARE @Before bigint,@After bigint,@Updated bigint
    DECLARE @Start_time datetime= GETUTCDATE()

    set @Before = (SELECT COUNT_BIG(*) from AdventureWorksDW.dbo.ProductDimension) 

    DECLARE @log_ids as table(id bigint)

    INSERT INTO AdventureWorksDW.dbo.ETL_Process_Log(TableName,ETL_start,NumberOfRecordsBefore)
    OUTPUT INSERTED.ID into @log_ids
    SELECT 'ProductDimension', @Start_time, @Before

    declare @LogId bigint = (select top 1 id from @log_ids)

    ;with source_product as(
        SELECT p.ProductID ,
            p.[Name],
            p.ProductNumber,
            p.FinishedGoodsFlag ,
            p.Color ,
            pc.ProductCategoryID,
            pc.Name as ProductCategoryName ,
            psc.ProductSubCategoryID,
            psc.Name as ProductSubcategoryName ,
            pm.ProductModelID  ,
            pm.Name as ProductModelName,
            pmpdc.ProductDescriptionID ,
            pd.Description as ProductDescription ,
            pm.CatalogDescription ,
            pm.Instructions ,
            p.ModifiedDate ,
            p.[Weight] ,
            p.WeightUnitMeasureCode,
            p.[Size] ,
            sod.UnitPrice,
            sod.UnitPriceDiscount as UnitDiscountPrice ,
            GETUTCDATE() as ETL_Load_Time

        from ((((((AdventureWorks2022.Sales.SalesOrderDetail as sod 
        left join AdventureWorks2022.Production.Product as p on
        sod.ProductID = p.ProductID)   
        join AdventureWorks2022.Production.ProductSubCategory as psc on 
        p.ProductSubcategoryID = psc.ProductSubcategoryID)
        join AdventureWorks2022.Production.ProductCategory as pc on 
        psc.ProductCategoryID = pc.ProductCategoryID)
        join AdventureWorks2022.Production.ProductModel as pm ON
        p.ProductModelID = pm.ProductModelID)
        join AdventureWorks2022.Production.ProductModelProductDescriptionCulture as pmpdc on
        pmpdc.ProductModelID = pm.ProductModelID )
        join AdventureWorks2022.Production.ProductDescription as pd on 
        pd.ProductDescriptionID = pmpdc.ProductDescriptionID)
    )
    INSERT INTO AdventureWorksDW.dbo.ProductDimension
    select sp.*
    from source_product as sp
    left join AdventureWorksDW.dbo.ProductDimension as pd on sp.ProductID = pd.ProductID  
    where pd.SKey is null;

    UPDATE AdventureWorksDW.dbo.ETL_Process_Log
        set CheckpointStatus = 'insert Completed'
    where id = @LogId

    set @After = (SELECT COUNT_BIG(*) from AdventureWorksDW.dbo.ProductDimension)

    set @Updated = @After - @Before

    UPDATE AdventureWorksDW.dbo.ETL_Process_Log
    SET CheckpointStatus = 'Completed',
        NumberOfRecordsAfter = @After,
        NumberOfRecordsModified = @Updated,
        LastModifiedDate = GETUTCDATE()
    WHERE id = @LogId





END

Commands completed successfully.

Total execution time: 00:00:00.014

- Store procedure for the shipping dimension

In [18]:
CREATE OR ALTER PROCEDURE ETL_Shipping 
AS
BEGIN



    DECLARE @count_before bigint, @count_after bigint, @count_updated bigint
    DECLARE @start_date datetime = GETUTCDATE()

    SET @count_before = (SELECT COUNT_BIG(*) FROM AdventureWorksDW.dbo.ShipingDimension)

    -- Креирање на табеларна променлива која ќе ни послужи во неа да внесеме податоци
    DECLARE @log_ids as table (id bigint)

    INSERT INTO AdventureWorksDW.dbo.ETL_Process_Log(TableName, ETL_start, NumberOfRecordsBefore)
    OUTPUT INSERTED.ID INTO @log_ids
    SELECT 'ShippingDimension', @start_date, @count_before
    
    DECLARE @LogId as bigint = (select top 1 id from @log_ids)


    ;With ship_method_source as (
    select sm.ShipMethodID,
        sm.[Name],
        sm.ShipBase,
        sm.ShipRate,
        poh.ShipDate,
        poh.[Status],
        GETUTCDATE() as ETL_Load_Time
        from AdventureWorks2022.Purchasing.PurchaseOrderHeader as poh 
        left join AdventureWorks2022.Purchasing.ShipMethod as sm 
        on poh.ShipMethodID = sm.ShipMethodID )
    INSERT INTO AdventureWorksDW.dbo.ShipingDimension
    select sms.*
    from ship_method_source as sms
    left join AdventureWorksDW.dbo.ShipingDimension as sd on sms.ShipMethodID = sd.ShipMethodID
    where sd.SKey is NULL ; 

    UPDATE AdventureWorksDW.dbo.ETL_Process_Log
    SET CheckpointStatus = 'Insert new completed'
    WHERE id = @LogId

    set @count_after = (SELECT count_big(*) FROM AdventureWorksDW.dbo.ShipingDimension)
    set @count_updated = @count_after - @count_before


    -- Ажурирање на лог табелата
    UPDATE AdventureWorksDW.dbo.ETL_Process_Log
    SET CheckpointStatus = 'Completed',
        NumberOfRecordsAfter = @count_after,
        NumberOfRecordsModified = @count_updated,
        LastModifiedDate = GETUTCDATE()
    WHERE id = @LogId


END
    




Commands completed successfully.

Total execution time: 00:00:00.009

- Creating a procedure for the fact table

In [9]:
CREATE OR ALTER PROCEDURE ETL_Order_Fact_Table
AS
BEGIN

    ;with fact_cte as(
        SELECT soh.TerritoryID,
        sod.ProductID, 
        soh.ShipMethodID,
        DAY(soh.OrderDate) as [Day],
        MONTH(soh.OrderDate) as [Month],
        YEAR(soh.OrderDate)  as  [Year],
        sod.OrderQty,
        sod.UnitPrice
        FROM (AdventureWorks2022.Sales.SalesOrderDetail as sod 
        JOIN AdventureWorks2022.Sales.SalesOrderHeader as soh 
        ON sod.SalesOrderID = soh.SalesOrderID)
    )SELECT 
            fcte.TerritoryID,
            fcte.ProductID,
            fcte.ShipMethodID,
            fcte.Day,
            fcte.Month,
            fcte.Year,
            SUM(fcte.OrderQty) AS TotalQuantity,
            SUM(fcte.OrderQty * fcte.UnitPrice) AS TotalAmount
    INTO #Tmp_FactOrder
    FROM fact_cte fcte
    GROUP BY fcte.TerritoryID,
            fcte.ProductID,
            fcte.ShipMethodID,
            fcte.Day,
            fcte.Month,
            fcte.Year;


    INSERT INTO AdventureWorksDW.dbo.OrderFactTable(TerritoryDimKey ,ProductDimKey,DateDimKey, ShippingDimKey, OrderQuantity ,TotalAmount)
    select top 100 td.SKey as TerritoryDimKey, pd.SKey as ProductDimKey, dd.SKey as DateDimKey,sd.SKey as ShippingDimKey, fo.TotalQuantity, fo.TotalAmount
    FROM AdventureWorksDW.dbo.TerritoryDim as td join #Tmp_FactOrder as fo on td.TerritoryID = fo.TerritoryID
    JOIN AdventureWorksDW.dbo.ProductDimension as pd on pd.ProductID= fo.ProductID 
    JOIN AdventureWorksDW.dbo.ShipingDimension as sd on sd.ShipMethodID = fo.ShipMethodID
    JOIN AdventureWorksDW.dbo.DateDimension as dd on dd.[Day] = fo.Day and dd.[Month] = fo.Month and dd.[Year] = fo.Year
    Left join AdventureWorksDW.dbo.OrderFactTable as oft on 
    oft.TerritoryDimKey = td.SKey and 
    oft.ProductDimKey = pd.SKey and 
    oft.ShippingDimKey= sd.SKey and 
    dd.SKey= oft.DateDimKey 
    where oft.ProductDimKey is NULL;


END

Commands completed successfully.

Total execution time: 00:00:00.008